<a href="https://colab.research.google.com/github/graviada/colabRepo/blob/master/2022/DataAnalysisMethods%20(6%2C%202022)/DataAnalysisMethods.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### Задание 2

Компании:
> * Heineken
> * Anheuser-Busch InBev
> * Carlsberg
> * Brown-Forman
> * Asahi
> * Pernod Ricard
> * Compañía Cervecerías Unidas





In [50]:
pip install yfinance

In [51]:
import pandas as pd
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import yfinance as yf
import numpy as np

from math import log
from plotly.subplots import make_subplots

In [52]:
def addline(fig, type="h", x0=0, x1=1, y0=0, y1=1):
  
  if type == "h":
    fig.add_shape(type='line',
                  x0 = x0,
                  x1 = x0,
                  y0 = y0,
                  y1 = y1,
                  line = dict(color="blue", dash="dashdot"),
                  opacity = 0.8)
  elif type == "v":
    fig.add_shape(type='line',
                  x0 = x0,
                  x1 = x1,
                  y0 = y0,
                  y1 = y0,
                  line = dict(color="LightSeaGreen", dash="dashdot"),
                  opacity = 0.8)
  elif type == "r":
    fig.add_shape(type='rect',
                  x0 = x0,
                  x1 = x1,
                  y0 = y0,
                  y1 = y1,
                  fillcolor='goldenrod',
                  opacity = 0.2)
  return fig

In [53]:
heineken = yf.download('HEINY','2011-02-10','2022-03-22')[['Close', 'Volume']]
an_busch = yf.download('BUD','2011-02-10','2022-03-22')[['Close', 'Volume']]
carlsberg = yf.download('CABGY','2011-02-10','2022-03-22')[['Close', 'Volume']]
brown_for = yf.download('BF-B','2011-02-10','2022-03-22')[['Close', 'Volume']]
asahi = yf.download('AHKSY','2011-02-10','2022-03-22')[['Close', 'Volume']]
per_ric = yf.download('PRNDY','2011-02-10','2022-03-22')[['Close', 'Volume']]
comp_cer = yf.download('CCU','2011-02-10','2022-03-22')[['Close', 'Volume']]

[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed


In [54]:
names = ['heineken', 'an_busch', 'carlsberg', 'brown_for',
             'asahi', 'per_ric', 'comp_cer']

dfs = [heineken, an_busch, carlsberg, brown_for, asahi, per_ric, comp_cer]

In [55]:
for name in dfs:
  name = name.reset_index()

# Убираем строку с NA в данных компании
brown_for = brown_for.dropna()

In [56]:
# Создание объединенного датафрейма
df_final = pd.concat([df.add_prefix(name + '_') for name, df in zip(names, dfs)], axis=1)

df_final = df_final.reset_index()

In [57]:
# Удаление строк с нулевым объемом (Volume)
for name in names:
  df_final = df_final.drop(df_final[df_final[name + '_Volume'] == 0].index)

1. Агрегированная характеристика для каждой компании

In [58]:
def aggr_characteristic(df, names):
  df_char = pd.DataFrame()
  for name in names:
    i = 0
    df_char.insert(i, name + '_aggr', df[name + '_Close'] * df[name + '_Volume'])
    i += 1
  return df_char

In [59]:
df_char = aggr_characteristic(df_final, names)

length_df_char = len(df_char)

In [60]:
summa = []

for i in range(length_df_char):
  summ = 0
  for name in names:
    summ += df_char[name + '_aggr'].iloc[i]
  summa.append(log(summ))

df_char.insert(0, 'S', summa)

In [61]:
day_list = pd.Series([i for i in range(length_df_char)])

In [62]:
_layout = go.Layout(
    title={
        'text': 'График показателя S в полулогарифмическом масштабе',
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'},
    yaxis_title='ln(S)',
    xaxis_title='t, дни',
    width=700,
    height=700,
    plot_bgcolor='rgba(0,0,0,0)'
)
fig = go.Figure([go.Scatter(x=day_list, y=df_char.S, line=dict(color='LightSeaGreen', width=1.5))], layout=_layout)

fig = addline(fig, type= "r", y0=17, y1=21.2, x0=day_list.iloc[342], x1=day_list.iloc[1176])
fig = addline(fig, type= "r", y0=17, y1=21.2, x0=day_list.iloc[1477], x1=day_list.iloc[1654])
fig = addline(fig, type= "r", y0=17, y1=21.2, x0=day_list.iloc[1917], x1=day_list.iloc[1996])
fig = addline(fig, type= "r", y0=17, y1=21.2, x0=day_list.iloc[2438], x1=day_list.iloc[2567])

fig.update_xaxes(showline=True, linewidth=0.5, gridcolor='grey')
fig.update_yaxes(showline=True, linewidth=0.5, gridcolor='grey')

fig.show()

In [63]:
_layout = go.Layout(
    title={
        'text': 'График показателя S в полулогарифмическом масштабе',
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'},
    yaxis_title='ln(S)',
    xaxis_title='t, дни',
    width=600,
    height=700,
    plot_bgcolor='rgba(0,0,0,0)'
)

fig = go.Figure([go.Scatter(x=day_list.iloc[320:1176], y=df_char.S.iloc[320:1176], line=dict(color='LightSeaGreen', width=1.5))], 
                layout=_layout)

fig = addline(fig, type= "r", y0=17, y1=21.2, x0=day_list.iloc[436], x1=day_list.iloc[492])
fig = addline(fig, type= "r", y0=17, y1=21.2, x0=day_list.iloc[738], x1=day_list.iloc[865])
fig = addline(fig, type= "r", y0=17, y1=21.2, x0=day_list.iloc[1051], x1=day_list.iloc[1143])

fig.update_xaxes(showline=True, linewidth=0.5, gridcolor='grey')
fig.update_yaxes(showline=True, linewidth=0.5, gridcolor='grey')

fig.show()

2. Темпы роста

In [64]:
def k_rates_growth(S, t1, t2):
  return (log(S.iloc[t2] / S.iloc[t1])) / (t2 - t1)

def process_time(k):
  return 1 / k

In [65]:
t_dict = [[436, 492], [738, 865], [1051, 1143], [1477, 1654], [1917, 1996], [2438, 2567]]

for i in range(6):
  k = k_rates_growth(df_char.S, t_dict[i][0], t_dict[i][1])
  print('Темп роста на {} участке: {:.7f}'.format(i+1, k))
  print('Характерное время процесса: {:.5f}\n'.format(process_time(k)))

Темп роста на 1 участке: 0.0019270
Характерное время процесса: 518.95088

Темп роста на 2 участке: 0.0007371
Характерное время процесса: 1356.68933

Темп роста на 3 участке: 0.0006815
Характерное время процесса: 1467.39041

Темп роста на 4 участке: 0.0006792
Характерное время процесса: 1472.26991

Темп роста на 5 участке: 0.0012423
Характерное время процесса: 804.93527

Темп роста на 6 участке: 0.0007247
Характерное время процесса: 1379.79859



Длинные участки не брать, брать поменьше, рассматривать отдельно

### Задание 3
Определить, насколько каждая фирма соответствует структуре развития отрасли в целом. Для этого изобразить на одном графике в полулогарифмическом масштабе агрегированные характеристики фирм и интегральную характеристику всей отрасли. Существуют ли компании, которые живут по другим ритмам?

In [66]:
local_chars = pd.DataFrame()
j = 0
help_list = []

for name in names:
  for i in range(length_df_char):
    help_list.append(log(df_char[name + '_aggr'].iloc[i]))
  local_chars.insert(j, 'ln_' + name, help_list)
  j += 1
  del help_list[:]

In [67]:
_layout = go.Layout(
    title={
        'text': 'Сравнение интегральной характеристики S с агрегированными характеристиками фирм',
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'},
    yaxis_title='ln(Close * Volume) - 5',
    xaxis_title='t, дни',
    width=1000,
    height=700,
    plot_bgcolor='rgba(0,0,0,0)'
)

fig = go.Figure([
                 go.Scatter(x=day_list, y=df_char.S, line=dict(color='LightSeaGreen', width=1.5), name='S'),
                 go.Scatter(x=day_list, y=local_chars.ln_heineken + 0.6, line=dict(color='goldenrod', width=1.5), name='Heineken'),
                 go.Scatter(x=day_list, y=local_chars.ln_an_busch - 9, line=dict(color='#CAB39F', width=1.5), name='Anheuser-Busch InBev'),
                 go.Scatter(x=day_list, y=local_chars.ln_carlsberg - 9.5, line=dict(color='#56B4E9', width=1.5), name='Carlsberg'),
                 go.Scatter(x=day_list, y=local_chars.ln_brown_for - 21, line=dict(color='#afff10', width=1.5), name='Brown-Forman'),
                 go.Scatter(x=day_list, y=local_chars.ln_asahi - 22, line=dict(color='#f498c2', width=1.5), name='Asahi'),
                 go.Scatter(x=day_list, y=local_chars.ln_per_ric - 31, line=dict(color='grey', width=1.5), name='Pernod Ricard'),
                 go.Scatter(x=day_list, y=local_chars.ln_comp_cer - 40, line=dict(color='#ffcaaf', width=1.5), name='Compañía Cervecerías Unidas')
                 ], layout=_layout)

fig.update_xaxes(showline=True, linewidth=0.5, gridcolor='grey')
fig.update_yaxes(showline=True, linewidth=0.5, gridcolor='grey')

fig.show()

In [68]:
df_final.iloc[1331]

Date                2016-12-01 00:00:00
heineken_Close                36.279999
heineken_Volume                 72600.0
an_busch_Close                99.910004
an_busch_Volume               7462000.0
carlsberg_Close                   16.43
carlsberg_Volume               162500.0
brown_for_Close                   35.68
brown_for_Volume              1681250.0
asahi_Close                   17.290001
asahi_Volume                    23800.0
per_ric_Close                     20.49
per_ric_Volume                 324500.0
comp_cer_Close                     20.0
comp_cer_Volume                544400.0
Name: 1462, dtype: object

### Задание 4
Необходимо рассмотреть данные в аллометрической системе координат. Построить графики, где по оси абсцисс – натуральный логарифм интегральной характеристики (S), по оси ординат – натуральный логарифм агрегированного показателя фирмы. Выяснить, какие компании развиваются по общему закону, какие опережают отрасль, а какие отстают.

Квадратные графики, попробовать кум. сумму сделать 

In [69]:
# # кумулятивная сумма от агрегированного показателя 
# for name in names:
#   df_char['cum_' + name] = df_char['aggr_' + name].cumsum()

# # кумулятивная сумма от логарифма
# for name in names:
#   local_chars['cum_' + name] = local_chars['ln_' + name].cumsum()

In [70]:
fig = make_subplots(
    rows=3, cols=3,
    subplot_titles=('Heineken', 'Anheuser-Busch InBev', 'Carlsberg', 'Brown-Forman',
                   'Asahi', 'Pernod Ricard', 'Compañía Cervecerías Unidas'))

x_trace = df_char.S
clr = 'darkblue'

# fig.add_trace(go.Scatter(x=x_trace, y=df_char.cum_heineken, mode='markers', marker=dict(color=clr)), row=1, col=1)
# fig.add_trace(go.Scatter(x=x_trace, y=df_char.cum_an_busch, mode='markers', marker=dict(color=clr)), row=1, col=2)
# fig.add_trace(go.Scatter(x=x_trace, y=df_char.cum_carlsberg, mode='markers', marker=dict(color=clr)), row=1, col=3)
# fig.add_trace(go.Scatter(x=x_trace, y=df_char.cum_brown_for, mode='markers', marker=dict(color=clr)), row=2, col=1)
# fig.add_trace(go.Scatter(x=x_trace, y=df_char.cum_asahi, mode='markers', marker=dict(color=clr)), row=2, col=2)
# fig.add_trace(go.Scatter(x=x_trace, y=df_char.cum_per_ric, mode='markers', marker=dict(color=clr)), row=2, col=3)
# fig.add_trace(go.Scatter(x=x_trace, y=df_char.cum_comp_cer, mode='markers', marker=dict(color=clr)), row=3, col=1)

fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_heineken, mode='markers', marker=dict(color=clr)), row=1, col=1)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_an_busch, mode='markers', marker=dict(color=clr)), row=1, col=2)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_carlsberg, mode='markers', marker=dict(color=clr)), row=1, col=3)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_brown_for, mode='markers', marker=dict(color=clr)), row=2, col=1)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_asahi, mode='markers', marker=dict(color=clr)), row=2, col=2)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_per_ric, mode='markers', marker=dict(color=clr)), row=2, col=3)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_comp_cer, mode='markers', marker=dict(color=clr)), row=3, col=1)

fig.update_layout(
    width=800,
    height=800,
    plot_bgcolor='rgba(0,0,0,0)',
    title={
          'text': 'Данные в аллометрической системе координат',
          'xanchor': 'left'},
    showlegend=False)

fig.update_xaxes(showline=True, linewidth=0.5, gridcolor='grey')
fig.update_yaxes(showline=True, linewidth=0.5, gridcolor='grey')

fig.show()

In [71]:
def draw_4(name):
  _layout = go.Layout(
      title={
          'text': 'Данные в аллометрической системе координат',
          'y':0.9,
          'x':0.5,
          'xanchor': 'center',
          'yanchor': 'top'},
      yaxis_title='ln(' + name + '_Close * ' + name + '_Volume)',
      xaxis_title='ln(S)',
      width=700,
      height=700,
      plot_bgcolor='rgba(0,0,0,0)'
  )

  fig = go.Figure([go.Scatter(x=df_char.S, y=local_chars['ln_' + name], mode='markers', marker=dict(color='darkblue'))], layout=_layout)

  fig.update_xaxes(showline=True, linewidth=0.5, gridcolor='grey')
  fig.update_yaxes(showline=True, linewidth=0.5, gridcolor='grey')

  fig.show()

In [78]:
draw_4('comp_cer')

In [73]:
draw_4('an_busch')

https://plotly.com/python/subplots/

### Задание 5
Необходимо рассмотреть, как взаимодействуют компании между собой попарно. Для этого построить для каждой пары компаний логарифмическую систему координат, где по оси ординат – агрегированная характеристика одной компании, по оси абсцисс – агрегированная характеристика второй компании.
Возможные варианты взаимодействия:
>1. Дружественные отношения. - линейная
>
>2. «Хищник-жертва». - нелинейная
>
>3. Нейтральные отношения. - это когда полоска

Математические модели борьбы за существование
В. Вольтерра - для 5

In [244]:
fig = make_subplots(
    rows=2, cols=3,
    subplot_titles=('Anheuser-Busch InBev', 'Carlsberg', 'Brown-Forman',
                   'Asahi', 'Pernod Ricard', 'Compañía Cervecerías Unidas'))

x_trace = local_chars.ln_heineken
clr = 'green'

fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_an_busch, mode='markers', marker=dict(color=clr)), row=1, col=1)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_carlsberg, mode='markers', marker=dict(color=clr)), row=1, col=2)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_brown_for, mode='markers', marker=dict(color=clr)), row=1, col=3)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_asahi, mode='markers', marker=dict(color=clr)), row=2, col=1)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_per_ric, mode='markers', marker=dict(color=clr)), row=2, col=2)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_comp_cer, mode='markers', marker=dict(color=clr)), row=2, col=3)

fig.update_layout(
    width=1000,
    height=800,
    plot_bgcolor='rgba(0,0,0,0)',
    title={
          'text': 'Данные в логарифмической системе координат для компании Heineken',
          'xanchor': 'left'},
    showlegend=False)

fig.update_xaxes(showline=True, linewidth=0.5, gridcolor='grey')
fig.update_yaxes(showline=True, linewidth=0.5, gridcolor='grey')

fig.show()

In [245]:
fig = make_subplots(
    rows=2, cols=3,
    subplot_titles=('Heineken', 'Carlsberg', 'Brown-Forman',
                   'Asahi', 'Pernod Ricard', 'Compañía Cervecerías Unidas'))

x_trace = local_chars.ln_an_busch
clr = 'green'

fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_heineken, mode='markers', marker=dict(color=clr)), row=1, col=1)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_carlsberg, mode='markers', marker=dict(color=clr)), row=1, col=2)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_brown_for, mode='markers', marker=dict(color=clr)), row=1, col=3)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_asahi, mode='markers', marker=dict(color=clr)), row=2, col=1)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_per_ric, mode='markers', marker=dict(color=clr)), row=2, col=2)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_comp_cer, mode='markers', marker=dict(color=clr)), row=2, col=3)

fig.update_layout(
    width=1000,
    height=800,
    plot_bgcolor='rgba(0,0,0,0)',
    title={
          'text': 'Данные в логарифмической системе координат для компании Anheuser-Busch InBev',
          'xanchor': 'left'},
    showlegend=False)

fig.update_xaxes(showline=True, linewidth=0.5, gridcolor='grey')
fig.update_yaxes(showline=True, linewidth=0.5, gridcolor='grey')

fig.show()

In [246]:
fig = make_subplots(
    rows=2, cols=3,
    subplot_titles=('Heineken', 'Anheuser-Busch InBev', 'Brown-Forman',
                   'Asahi', 'Pernod Ricard', 'Compañía Cervecerías Unidas'))

x_trace = local_chars.ln_carlsberg
clr = 'green'

fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_heineken, mode='markers', marker=dict(color=clr)), row=1, col=1)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_an_busch, mode='markers', marker=dict(color=clr)), row=1, col=2)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_brown_for, mode='markers', marker=dict(color=clr)), row=1, col=3)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_asahi, mode='markers', marker=dict(color=clr)), row=2, col=1)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_per_ric, mode='markers', marker=dict(color=clr)), row=2, col=2)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_comp_cer, mode='markers', marker=dict(color=clr)), row=2, col=3)

fig.update_layout(
    width=1000,
    height=800,
    plot_bgcolor='rgba(0,0,0,0)',
    title={
          'text': 'Данные в логарифмической системе координат для компании Carlsberg',
          'xanchor': 'left'},
    showlegend=False)

fig.update_xaxes(showline=True, linewidth=0.5, gridcolor='grey')
fig.update_yaxes(showline=True, linewidth=0.5, gridcolor='grey')

fig.show()

In [247]:
fig = make_subplots(
    rows=2, cols=3,
    subplot_titles=('Heineken', 'Anheuser-Busch InBev', 'Carlsberg',
                   'Asahi', 'Pernod Ricard', 'Compañía Cervecerías Unidas'))

x_trace = local_chars.ln_brown_for
clr = 'green'

fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_heineken, mode='markers', marker=dict(color=clr)), row=1, col=1)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_an_busch, mode='markers', marker=dict(color=clr)), row=1, col=2)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_carlsberg, mode='markers', marker=dict(color=clr)), row=1, col=3)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_asahi, mode='markers', marker=dict(color=clr)), row=2, col=1)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_per_ric, mode='markers', marker=dict(color=clr)), row=2, col=2)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_comp_cer, mode='markers', marker=dict(color=clr)), row=2, col=3)

fig.update_layout(
    width=1000,
    height=800,
    plot_bgcolor='rgba(0,0,0,0)',
    title={
          'text': 'Данные в логарифмической системе координат для компании Brown-Forman',
          'xanchor': 'left'},
    showlegend=False)

fig.update_xaxes(showline=True, linewidth=0.5, gridcolor='grey')
fig.update_yaxes(showline=True, linewidth=0.5, gridcolor='grey')

fig.show()

In [248]:
fig = make_subplots(
    rows=2, cols=3,
    subplot_titles=('Heineken', 'Anheuser-Busch InBev', 'Carlsberg', 'Brown-Forman',
                   'Pernod Ricard', 'Compañía Cervecerías Unidas'))

x_trace = local_chars.ln_asahi
clr = 'green'

fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_heineken, mode='markers', marker=dict(color=clr)), row=1, col=1)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_an_busch, mode='markers', marker=dict(color=clr)), row=1, col=2)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_carlsberg, mode='markers', marker=dict(color=clr)), row=1, col=3)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_brown_for, mode='markers', marker=dict(color=clr)), row=2, col=1)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_per_ric, mode='markers', marker=dict(color=clr)), row=2, col=2)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_comp_cer, mode='markers', marker=dict(color=clr)), row=2, col=3)

fig.update_layout(
    width=1000,
    height=800,
    plot_bgcolor='rgba(0,0,0,0)',
    title={
          'text': 'Данные в логарифмической системе координат для компании Asahi',
          'xanchor': 'left'},
    showlegend=False)

fig.update_xaxes(showline=True, linewidth=0.5, gridcolor='grey')
fig.update_yaxes(showline=True, linewidth=0.5, gridcolor='grey')

fig.show()

In [250]:
fig = make_subplots(
    rows=2, cols=3,
    subplot_titles=('Heineken', 'Anheuser-Busch InBev', 'Carlsberg', 'Brown-Forman',
                   'Asahi', 'Compañía Cervecerías Unidas'))

x_trace = local_chars.ln_per_ric
clr = 'green'

fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_heineken, mode='markers', marker=dict(color=clr)), row=1, col=1)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_an_busch, mode='markers', marker=dict(color=clr)), row=1, col=2)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_carlsberg, mode='markers', marker=dict(color=clr)), row=1, col=3)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_brown_for, mode='markers', marker=dict(color=clr)), row=2, col=1)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_asahi, mode='markers', marker=dict(color=clr)), row=2, col=2)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_comp_cer, mode='markers', marker=dict(color=clr)), row=2, col=3)

fig.update_layout(
    width=1000,
    height=800,
    plot_bgcolor='rgba(0,0,0,0)',
    title={
          'text': 'Данные в логарифмической системе координат для компании Pernod Ricard',
          'xanchor': 'left'},
    showlegend=False)

fig.update_xaxes(showline=True, linewidth=0.5, gridcolor='grey')
fig.update_yaxes(showline=True, linewidth=0.5, gridcolor='grey')

fig.show()

In [249]:
fig = make_subplots(
    rows=2, cols=3,
    subplot_titles=('Heineken', 'Anheuser-Busch InBev', 'Carlsberg', 'Brown-Forman',
                   'Asahi', 'Pernod Ricard'))

x_trace = local_chars.ln_comp_cer
clr = 'green'

# for i in range(1, 3):
#   for j in range(1, 4):
#     fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_heineken, mode='markers', marker=dict(color=clr)), row=1, col=1)

fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_heineken, mode='markers', marker=dict(color=clr)), row=1, col=1)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_an_busch, mode='markers', marker=dict(color=clr)), row=1, col=2)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_carlsberg, mode='markers', marker=dict(color=clr)), row=1, col=3)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_brown_for, mode='markers', marker=dict(color=clr)), row=2, col=1)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_asahi, mode='markers', marker=dict(color=clr)), row=2, col=2)
fig.add_trace(go.Scatter(x=x_trace, y=local_chars.ln_per_ric, mode='markers', marker=dict(color=clr)), row=2, col=3)

fig.update_layout(
    width=1000,
    height=800,
    plot_bgcolor='rgba(0,0,0,0)',
    title={
          'text': 'Данные в логарифмической системе координат для компании Compañía Cervecerías Unidas',
          'xanchor': 'left'},
    showlegend=False)

fig.update_xaxes(showline=True, linewidth=0.5, gridcolor='grey')
fig.update_yaxes(showline=True, linewidth=0.5, gridcolor='grey')

fig.show()

### Задание 6